[Information Visualization Tutorials](https://infovis.fh-potsdam.de/tutorials/) · FH Potsdam · Summer 2020

# Tutorial 8: Geovisualization

In this last instalment of the information visualization tutorials we will be analyzing and visualizing geographic data; i.e., data that refers to geospatial entities. Geospatial entities can, for example, be particular places such as schools and libraries or political boundaries of cities or countries. Of course, this tutorial only scratches the surface. Consider this as a teaser into geovisualization, which in itself has become a branch of research and practice at the intersection of geography and visualization. We will only touch on a few basic steps to get your feet wet and hands dirty.


## 🛒 1. Prepare 

As you come to expect by now we first assemble our tools and then prepare the data. 

In [39]:
import altair as alt
import pandas as pd

### Install packages

For this tutorial we will continue to rely on Altair and Pandas, but add **GeoPandas**, which will help us to work with DataFrames that contain spatial entities to carry out geometric analysis on them. As before, the pip install command is carried out via the shell, which is indicated by the exclamation mark at the beginning of the line:

In [40]:
!pip install geopandas
import geopandas as gpd

To access the data of the OpenStreetMap, we will install the handy package **OSMPythonTools**:

In [41]:
!pip install OSMPythonTools

And finally, we will include **GeoPy**, which will help us turn addresses into geographic coordinates:

In [42]:
!pip install geopy

Once we have the tools assembled, we can get started working with geospatial data. There are actually plenty of formats used to record geospatial data, but GeoJSON has become an important standard for exchanging geospatial data on the web. However, please note that GeoPandas can actually load many other vector-based data formats used in digital cartography, such as shapefiles and GeoPackage.

### Import GeoJSON

Suppose we would like to get the geographic boundaries of Potsdam's districts, which happen to be published on Potsdam's Open Data Portal. Akin to how we would read a JSON file with Pandas, we can also use `read_file()` provided by GeoPandas simply by passing the URL to the data set of interest and get a geographic DataFrame back:

In [43]:
districts = gpd.read_file("https://opendata.potsdam.de/explore/dataset/statistische-bezirke-in-potsdam/download/?format=geojson")

If you replace `geojson` with `shp` at the end of above URL, you can also load this data from a shapefile format. Either way the data is going to be loaded into the data structure of a GeoDataFrame. The main difference between a regular Pandas DataFrame is that a GeoDataFrame features a `geometry` column, which is a geoseries containing the points, paths, and polygons for each row. For example, if each row represents one district, the respective geometries would probably contain the geospatial boundaries…

✏️ *Are you curious what the districts dataframe actually looks like? Take a look at it with the methods you know by now:* 

Geographically speaking, the districts are defined by their geographic shapes, which are represented as polygons, each of which is a list of tuples of geographic coordinates. Next we add information about schools in Potsdam:

In [44]:
schools = gpd.read_file("https://opendata.potsdam.de/explore/dataset/schulen/download/?format=geojson")

✏️ *Have a look at the schools as well, and compare the contents of the `geometry` columns in schools and districts. Do you notice anything?*

### Query OpenStreetMap

OpenStreetMap (OSM) is "a collaborative project to create a free editable map of the world". As such it has millions of contributing users who have been collecting, updating and refining map data for over 15 years, which has generated a vastly comprehensive source of geographic data. It is by no means complete—whatever this would mean—but it is an impressively large geographic database and, of course, a map in itself, too.

To get a list of libraries in Potsdam (according to the OSM), we first need to find the right Potsdam. For this we use the geocoding powers of OSM through the `Nominatim` search service:

In [45]:
from OSMPythonTools.nominatim import Nominatim
nominatim = Nominatim()
city = nominatim.query('Potsdam, Germany')
city.areaId()

3600062369

OpenStreetMap has its own kind of query language, which is quite compact and can also be a source for errors. To make query formulation easier, you can either use the web interface [overpass turbo](http://overpass-turbo.eu) or the `overpassQueryBuilder`, which provides access to the main parameters:

In [46]:
from OSMPythonTools.overpass import overpassQueryBuilder

library_query = overpassQueryBuilder(
    area=city.areaId(), # the query can be contrained by an area of an item
    elementType='node', # which are points (OSM also has ways and relations)
    # the selector in the next line is really the heart of the query:
    selector='"amenity"="library"', # we're looking for libraries
    out='body', # body indicates that we want the data, not just the count
    includeGeometry=True # and we want the geometric information, too
)

library_query

'area(3600062369)->.searchArea;(node["amenity"="library"](area.searchArea);); out body geom;'

The output of above cell is the compact version of the query, which is carried out in the next step:



In [47]:
from OSMPythonTools.overpass import Overpass
overpass = Overpass()

lib_data = overpass.query(library_query)

The variable `lib_data` now already contains the result from the query against OSM. Let's have a look at it. With `nodes()` we can access the retrieved points. Let's take a look at the first entry:

In [48]:
lib_data.nodes()[0].tags()

{'addr:city': 'Potsdam',
 'addr:country': 'DE',
 'addr:housenumber': '5',
 'addr:postcode': '14469',
 'addr:street': 'Kiepenheuerallee',
 'amenity': 'library',
 'contact:email': 'bibliothek@fh-potsdam.de',
 'contact:fax': '+49 331 580 2229',
 'contact:phone': '+49 331 580 2211',
 'contact:website': 'https://www.fh-potsdam.de/informieren/organisation/wiss-einrichtungen/bibliothek/bibliothek-news/',
 'name': 'Hochschulbibliothek',
 'opening_hours': 'Mo-Fr 09:00-19:00; Sa 09:00-14:30; PH,Su off; 2019 Dec 21-2020 Jan 01 off',
 'opening_hours:url': 'https://www.fh-potsdam.de/informieren/organisation/wiss-einrichtungen/bibliothek/wir-ueber-uns/oeffnungszeiten/',
 'operator': 'Fachhochschule Potsdam',
 'operator:type': 'public',
 'operator:wikidata': 'Q896706',
 'operator:wikipedia': 'de:Fachhochschule Potsdam',
 'ref:isil': 'DE-525',
 'wheelchair': 'limited'}

Similarly, we can also access the geometry, which in this case is just a point:

In [49]:
lib_data.nodes()[0].geometry()

{"coordinates": [13.051358, 52.41372], "type": "Point"}

Next, we use the compact form of a list comprehension to extract the libraries' names and coordinates:


In [50]:
libraries = [ (lib.tag("name"), lib.geometry() ) for lib in lib_data.nodes()]

… which we turn into a GeoDataFrame. By naming the second column `geometry` we indicate towards GeoPandas to interpret the coordinates as geographic locations:

In [51]:
libraries = gpd.GeoDataFrame(libraries, columns = ['name', 'geometry'])

Let's repeat the process to retrieve Berlin's trees (as recorded by the OSM community):

In [52]:
# 1. prepare query (and directly include the location lookup)
tree_query = overpassQueryBuilder(
    area=nominatim.query('Berlin, Germany').areaId(),
    elementType='node',
    selector='"natural"="tree"', 
    out='body', 
    includeGeometry=True
)

# 2. execute query (and give it a bit more time to finish)
tree_data = overpass.query(tree_query, timeout=60)

# 3. get ids and coordinates of trees
tree_locs = [ (tree.id(), tree.geometry()) for tree in tree_data.nodes()]

# 4. create GeoDataFrame
trees = gpd.GeoDataFrame(tree_locs, columns=["id", "geometry"])

trees.head()

id                   geometry
0  21487172  POINT (13.35177 52.51431)
1  26908663  POINT (13.34627 52.47173)
2  27306554  POINT (13.30086 52.52252)
3  27306733  POINT (13.30062 52.52235)
4  30429119  POINT (13.30101 52.52255)

What are you interested in? You may want to consult the [Overpass API](https://wiki.openstreetmap.org/wiki/Overpass_API) or play around with [overpass turbo](http://overpass-turbo.eu): 

✏️ *Copy above code into the cell below and adjust the query and variable names according to your interest:*

## 📍 2. Process

<!-- Two important processing steps are turning addresses into geolocations and aggregating geospatial data to feed into choropleth maps. -->

One important processing step is turning addresses into geolocations.

### Geocoding addresses

A typical challenge before actually visualizing geographic data is to extract the geographic coordinates of items of interest (may they be trees or libraries). When loading GeoJSON files or querying OpenStreetMap the geometries are naturally already included. However, oftentimes we may only have street addresses or the names of geographic entities such as cities or points of interests, which cannot be directly used to derive positions on a map. Yet, intuitively speaking names of places and street addresses are unique ways of identifying locations. To turn such geographic strings into geographic tuples we rely on geocoding. In short: geocoding translates an address or place name into geographic coordinates. 

There are plenty of commercial geocoders out there, but for the purpose of this tutorial we simply use OpenStreetMap's Nominatem service via the handy GeoPy package. (We could also stick to the OSMPythonTools that we already used above, but GeoPy has some handy ways of carrying out multiple geocoding steps in a batch.)


In [53]:
# import Nominatim as geopy geocoder
from geopy.geocoders import Nominatim

# register custom user agent (commercial services may also require an API key)
geocoder = Nominatim(user_agent="Information Visualization Tutorial · FH Potsdam")

Let's start with an address, students of FH Potsdam might be familiar with:

In [54]:
loc = geocoder.geocode("Kiepenheuerallee 5, 14469 Potsdam")
print(loc)

Campus Fachhochschule Potsdam, 5, Kiepenheuerallee, Bornstedt, Potsdam Nord, Potsdam, Brandenburg, 14469, Deutschland


We can access the geographic coordinates one by one:

In [55]:
print((loc.latitude, loc.longitude))

(52.4123583, 13.050748548573427)


Note that we can also use a name of a place; however, in this case the coordinates do not refer to the street address, but the center of the place:

In [56]:
loc = geocoder.geocode("Fachhochschule Potsdam")
print((loc.latitude, loc.longitude))

(52.4121432, 13.0507812)


✏️ *Give the geocoder a try and issue a geocoding request for an address or placename of your choice:* 

Let's proceed with a dataset containing multiple places. Do you remember the childcare dataset we loaded in the data wrangling tutorial? The dataset actually did not include geospatial coordinates, but street addresses! Let's load the CSV again into a DataFrame:

In [57]:
kitas = pd.read_csv("https://opendata.potsdam.de/explore/dataset/kitaboerse-20161108/download/", sep=";")

The `hausnummer` column contains some non-numerical items such as months (for no apparent reason). This will cause errors later during geocoding. In the following we extract the first number encountered in the `hausnummer` cells. Some kitas have multiple house numbers, for the purpose of this tutorial one will suffice.

In [58]:
# parameter of extract is a regular expression that the first set of digits 
kitas.hausnummer = kitas.hausnummer.str.extract('(\d+)')

# in some cases the value is not a number, which we will with zeros
kitas.hausnummer = kitas.hausnummer.fillna(0)

Geocoding can take a bit of time, so we limit ourselves to just a few random entries here:


In [59]:
kitas = kitas.sample(20)

✏️ *If you have a bit of time, increase above number or simply comment out the line to analyze all kitas in Potsdam*

Note that the address information is spread across three columns: `strasse`, `hausnummer`, `postleitzahl`.

We will turn them into one column, with which we query the geocoder. For the purpose of this tutorial, we keep the remaining data at a minimum and thus only keep the names of the kitas and their capacities:

In [60]:
kitas

name_der_kindertagesbetreuungseinrichtung  ...       link_zu_anmeldeinformationen_der_einrichtung
132                              Spielgruppe Waldstadt  ...                        http://pbhev.de/?page_id=21
21                                   Rappelkiste, Kita  ...                  http://www.rappelkiste-potsdam.de
17                                    Flotowkids, Hort  ...                     http://www.kita-flotow-kids.de
28                                Die Buntstifte, Hort  ...  http://www.lindenpark.de/SPI_Potsdam/die-bunts...
135  Tagespflegepersonen FidL - Frauen in der Leben...  ...         http://fidl.de/kinderbetreuung/tagespflege
106                                   Nimmerland, Hort  ...  http://www.elternverein-zwergenland.de/wp-cont...
109                                  Zauberstein, Kita  ...  http://www.lsb-sportservice.de/files/antrag_au...
99       Evangelische Kindertagesstätte Regenbogenland  ...  http://www.hoffbauer-bildung.de/kita-regenboge...
67                               Am Heiligen See, Kita  ...  https://www.ejf.de/einrichtungen/kindertagesst...
5    Nuthegeister, AWO, Hort für hör-, sprach-, ler...  ...  http://www.awo-potsdam.de/einrichtungen-und-di...
78              Elterninitiativkita Butzemannhaus e.V.  ...  http://butzemannhaus.grossglienicke.de/index.html
26                                    Zauberwald, Kita  ...                      http://www.kita-zauberwald.de
124                                Spielgruppe drEKidZ  ...                http://anmeldung.die-kinderwelt.com
59                            Hort der Förderschule 18  ...  http://foerderhort-potsdam.froebel.info/fuer-e...
101                 Montessori Kinderhaus Potsdam-West  ...  http://www.montessori-kinderhaus-potsdam.de/an...
2          AKi an der Hanna-von-Pestalozza-Grundschule  ...  http://butzemannhaus.grossglienicke.de/Materia...
18         first steps Deutsch-Englischer Kindergarten  ...  http://www.firststeps-kita.de/aufnahme/anmeldu...
126                            Weberspatzen, AWO, Hort  ...  http://www.awo-potsdam.de/einrichtungen-und-di...
64                                     Sternchen, Kita  ...  http://sternchen-potsdam.froebel.info/fuer-elt...
107                                      Geolino, Kita  ...  http://www.hoffbauer-bildung.de/kita-geolino/a...

[20 rows x 49 columns]

In [61]:
# names of the childcare places
names = kitas["name_der_kindertagesbetreuungseinrichtung"]

# the capacity of the kitas; which we turn into integers
capac = kitas["platze_unbefristet"].fillna(0).astype(int)

# columns containing address information
addr = ['strasse', 'hausnummer', 'postleitzahl']

# we join the values in the three columns for each row
addresses = kitas[addr].apply(lambda row: ' '.join(row.values.astype(str)), axis=1)

# the dataframe we will use
kitas = pd.DataFrame({'name': names, 'capacity': capac, 'address': addresses})
kitas

name  ...                              address
132                              Spielgruppe Waldstadt  ...           Ginsterweg 3 14478 Potsdam
21                                   Rappelkiste, Kita  ...      Liefelds Grund 23 14478 Potsdam
17                                    Flotowkids, Hort  ...          Flotowstr. 10 14480 Potsdam
28                                Die Buntstifte, Hort  ...          Steinstr. 104 14480 Potsdam
135  Tagespflegepersonen FidL - Frauen in der Leben...  ...            Alleestr. 1 14469 Potsdam
106                                   Nimmerland, Hort  ...      Karl-Marx-Str. 72 14482 Potsdam
109                                  Zauberstein, Kita  ...       Berliner Str. 27 14467 Potsdam
99       Evangelische Kindertagesstätte Regenbogenland  ...        Hubertusdamm 50 14480 Potsdam
67                               Am Heiligen See, Kita  ...             Seestr. 43 14467 Potsdam
5    Nuthegeister, AWO, Hort für hör-, sprach-, ler...  ...          Bisamkiez 107 14478 Potsdam
78              Elterninitiativkita Butzemannhaus e.V.  ...        Seepromenade 54 14476 Potsdam
26                                    Zauberwald, Kita  ...      Liefelds Grund 27 14478 Potsdam
124                                Spielgruppe drEKidZ  ...   Konrad-Wolf-Allee 27 14480 Potsdam
59                            Hort der Förderschule 18  ...       Zum Teufelssee 6 14478 Potsdam
101                 Montessori Kinderhaus Potsdam-West  ...     Knobelsdorffstr. 7 14471 Potsdam
2          AKi an der Hanna-von-Pestalozza-Grundschule  ...         Hechtsprung 14 14476 Potsdam
18         first steps Deutsch-Englischer Kindergarten  ...  Ludwig-Richter-Str. 9 14467 Potsdam
126                            Weberspatzen, AWO, Hort  ...          Weberplatz 13 14482 Potsdam
64                                     Sternchen, Kita  ...      Ziolkowskistr. 47 14480 Potsdam
107                                      Geolino, Kita  ...      Telegrafenberg 33 14473 Potsdam

[20 rows x 3 columns]

Now let's turn addresses into geometries! For each cell in the address column, a query against OSM will be triggered; to spread out the load we use a RateLimiter provided by GeoPy:

In [62]:
from geopy.extra.rate_limiter import RateLimiter

# add a delay of one second between each geocoding request
geocode = RateLimiter(geocoder.geocode, min_delay_seconds=1)

Next we invoke the geocoder and apply it to the address column (depending on how many entries are to be geocoded, this can take a while):

In [63]:
# apply geocoding to address column; store responses in location column 
kitas['location'] = kitas['address'].apply(geocode)

There might be some kitas that have not location information, i.e., for which the geocoder was note able to identify latitude and longitude. We only keep those rows that have location information, i.e., that are `notnull()`:

In [64]:
kitas = kitas[kitas['location'].notnull()]

After that we use one list comprehension to extract latitudes and longitudes from the locations column, which we will then use to transform the DataFrame into a GeoDataFrame featuring its own `geometry` column:

In [65]:
# create empty columns for coordinates
kitas["lat"] = None
kitas["lon"] = None

# extract lat and lon from locations via one list comprehensions
kitas[['lat', 'lon']] = [ (loc.latitude, loc.longitude) for loc in kitas['location'] ]

# # create GeoDataFrame, pointing explicitly to lon and lat columns
kitas = gpd.GeoDataFrame(kitas, geometry=gpd.points_from_xy(kitas.lon, kitas.lat))

# # remove superfluous columns that are not needed anymore
kitas = kitas.drop(columns=['location', 'lat', 'lon'])

kitas

name  ...                   geometry
132                              Spielgruppe Waldstadt  ...  POINT (13.09033 52.36659)
21                                   Rappelkiste, Kita  ...  POINT (13.09383 52.35947)
17                                    Flotowkids, Hort  ...  POINT (13.13760 52.38271)
28                                Die Buntstifte, Hort  ...  POINT (13.14418 52.38368)
135  Tagespflegepersonen FidL - Frauen in der Leben...  ...  POINT (13.05937 52.40886)
106                                   Nimmerland, Hort  ...  POINT (13.12186 52.39552)
109                                  Zauberstein, Kita  ...  POINT (13.07188 52.40378)
99       Evangelische Kindertagesstätte Regenbogenland  ...  POINT (13.13799 52.38445)
67                               Am Heiligen See, Kita  ...  POINT (13.07233 52.41026)
5    Nuthegeister, AWO, Hort für hör-, sprach-, ler...  ...  POINT (13.09907 52.37246)
78              Elterninitiativkita Butzemannhaus e.V.  ...  POINT (13.10602 52.45766)
26                                    Zauberwald, Kita  ...  POINT (13.09256 52.35926)
124                                Spielgruppe drEKidZ  ...  POINT (13.13893 52.36830)
59                            Hort der Förderschule 18  ...  POINT (13.09042 52.36096)
101                 Montessori Kinderhaus Potsdam-West  ...  POINT (13.02383 52.38774)
2          AKi an der Hanna-von-Pestalozza-Grundschule  ...  POINT (13.10345 52.46618)
18         first steps Deutsch-Englischer Kindergarten  ...  POINT (13.07678 52.41135)
126                            Weberspatzen, AWO, Hort  ...  POINT (13.09499 52.39479)
64                                     Sternchen, Kita  ...  POINT (13.14013 52.37705)
107                                      Geolino, Kita  ...  POINT (13.06411 52.38234)

[20 rows x 4 columns]

## 🗺 3. Present

When we have geospatial data readily available as GeoDataFrames, we can now map them with Altair. 

(There are other mapping libraries for Python, such as [Folium](https://python-visualization.github.io/folium/), that provide additional functionalities. Altair's geovis features are basic, but do provide some variety of techniques and have the benefit to work consistently with the other chart types we covered.)


### Markers on maps

A simple start is placing locations on a base map and adding a bit of further information via tooltips. Let's do this with Potsdam's schools! First, we can have another look at the attributes:


In [66]:
schools.head(3)

status schulnum_1 schulnumme  ...  planungsra schulform                   geometry
0  Aktiv     120790          1  ...         601        OG  POINT (13.07798 52.38221)
1  Aktiv     401262      10/30  ...         602         F  POINT (13.09354 52.37393)
2  Aktiv     600027         15  ...         302       ZBW  POINT (13.05796 52.40132)

[3 rows x 15 columns]

This gives us plenty of aspects to visualize. 

We will now create a simple map with markers in the form of an  Altair chart consisting of two layers:

1.   The `districts` form the lower layer representing their boundaries and the overall geographic shape of Potsdam
2.   The `schools` are the points of interests that are displayed on top

When putting the two layers together they should actually refer to the same geographic location to make sense. Here the districts and schools both refer to Potsdam. Also note that the order when the charts are added together determines the vertical order: first the basemap and then markers on top.

In [67]:
# 1.  mark_geoshape transparently uses the geometry column
basemap = alt.Chart(districts).mark_geoshape(
    # add some styling to reduce the salience of the basemap
    fill="lightgray", stroke="darkgray"
).properties(width=600, height=600)

# 2.  we use mark_circle to have more control over visual variables
markers = alt.Chart(schools).mark_circle(opacity=1).encode(
    # point latitude & longitude to coordinates in geometry column
    longitude='geometry.coordinates[0]:Q',
    latitude='geometry.coordinates[1]:Q',
    tooltip=['schulname', 'strasse', 'trager'],
)

# combine the two layers 
basemap + markers

alt.LayerChart(...)

✏️ *How about changing the color of the dots according to `trager` or `schulform`?*

### Graduated symbol maps

This technique adjusts the visual features of markers to encode quantitative data dimensions. For example, we can use varying sizes of circles to represent the capacities of Potsdam's kitas. We use the same two-layer structure we used above:

In [68]:
basemap = alt.Chart(districts).mark_geoshape(
    fill="lightgray", stroke="darkgray"
).properties(width=600, height=600)

markers = alt.Chart(kitas).mark_circle(opacity=1).encode(
    longitude='geometry.coordinates[0]:Q',    
    latitude='geometry.coordinates[1]:Q',    
    tooltip=['name:N', 'address:N', 'capacity:Q'],
    size="capacity:Q"
)

basemap + markers

alt.LayerChart(...)

### Dot density maps

When we are dealing with thousands elements, we are reaching perceptual and technical limitations. One way to mitigate the technical limitations is to take a sample of the elements, large enough to see overall patterns. This is what we are now doing with Berlin's trees, of which there are far too many to display them all individually, however, a sample might still be informative:

In [69]:
# by default Altair only handles max number of 5000 items
# the following line disables this limitation, read more here:
# https://altair-viz.github.io/user_guide/faq.html#maxrowserror-how-can-i-plot-large-datasets
alt.data_transformers.disable_max_rows()

treemap = alt.Chart(trees.sample(n=10000)).mark_circle(
    # reduce the visual presence of each element
    size=5,
    # with a low dot opacity we can use overplotting to indicate densities
    opacity=.25,
    # a natural choice
    color="green"
).encode(
    longitude='geometry.coordinates[0]:Q', 
    latitude='geometry.coordinates[1]:Q'    
).properties(width=600, height=600)

treemap

alt.Chart(...)

✏️  *Add a baselayer underneath with Berlin's districts; the Technologiestiftung Berlin offers [spatial data in various shapes and sizes](https://lab.technologiestiftung-berlin.de/projects/spatial-units/en/). Hint: you might have to flip the [winding order](https://altair-viz.github.io/user_guide/data.html#winding-order) of the geometries.*

### Choropleth maps

Finally, let's create the geovisualization that uses the fill color of geospatial shapes to encode quantitative data. To illustrate this, we will visualize the population densities around the world. We will use area and population information from GeoNames and get the geographic shapes of countries from DataHub.

In [70]:
# load country data from geonames 
geonames = pd.read_csv("https://www.geonames.org/countryInfoCSV", sep='\t')
# select four columns
geonames = geonames[['name', 'iso alpha3', 'areaInSqKm', 'population']]
# set index to country code
geonames = geonames.set_index("iso alpha3")

geonames.head()

name  areaInSqKm  population
iso alpha3                                              
AND                      Andorra       468.0       77006
ARE         United Arab Emirates     82880.0     9630959
AFG                  Afghanistan    647500.0    37172386
ATG          Antigua and Barbuda       443.0       96286
AIA                     Anguilla       102.0       13254

Next we collect the geographic boundaries and `simplify` them a bit, as they have more detail than what we need here:

In [71]:
# load country's polygons from datahub
polygons = gpd.read_file("https://datahub.io/core/geo-countries/r/countries.geojson")
# remove country names, as we have them already
polygons = polygons.drop(columns=["ADMIN"])
# set index to country code
polygons = polygons.set_index("ISO_A3")
# reduce the complexity of the shapes
polygons.geometry = polygons.geometry.simplify(.1)

polygons.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 255 entries, ABW to ZWE
Data columns (total 1 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   geometry  255 non-null    geometry
dtypes: geometry(1)
memory usage: 4.0+ KB


As both DataFrames use the three-letter country codes as indices we can join them like this:

In [72]:
# inner means that we keep only those countries
# for which we have geometric and attribute data
countries = polygons.join(geonames, how='inner')

countries.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 238 entries, ABW to ZWE
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   geometry    238 non-null    geometry
 1   name        238 non-null    object  
 2   areaInSqKm  238 non-null    float64 
 3   population  238 non-null    int64   
dtypes: float64(1), geometry(1), int64(1), object(1)
memory usage: 9.3+ KB


Visualizing area or population in a choropleth map, arguably, makes little sense. So let's compute population densities:

In [73]:
countries["density"] = countries["population"] / countries["areaInSqKm"]

Keep only those countries with valid density value and turn these densities into integers:

In [74]:
countries = countries[countries['density'].notna()]
countries.density = countries.density.round(0).astype(int)

There is one ‘country’ that is not really one, which is Antarctica. We'll remove this from the list here.

In [75]:
countries = countries.drop("ATA")

Finally, we draw the chart using Altair's `mark_geoshape()` method. The distribution of densities is highly skewed, due to very small countries with relatively high population numbers, such as Monaco. To spread out the low and high density values we use a logarithmic scale and set the domain between 1 and 1000. Note that the domain has to end in a multiple of the base, which is by default 10.

In [76]:
alt.Chart(countries).mark_geoshape().encode(
    color=alt.Color('density', scale=alt.Scale(type="log", domain=[1,1000] )),
    tooltip=['name', 'areaInSqKm', 'population', 'density']
).project(
  # enter different projection here
).properties(
    width=800,
    height=600
)

alt.Chart(...)

The map is shown in the default Mercator projection, which particularly distorts the area sizes of North America, Europe and Russia in contrast to Africa, Southern Asia and parts of South America.

✏️ *Change the projection used above to one that does not distort area sizes as much ([see this list for options](https://vega.github.io/vega-lite/docs/projection.html#projection-types)).* 

## Sources

Tutorials & Documentation
- [Specifying Geospatial Data in Altair — Altair 4.1.0 documentation](https://altair-viz.github.io/user_guide/data.html#geospatial-data)
- [GeoPandas](https://geopandas.org)
- [OSMPythonTools](https://github.com/mocnik-science/osm-python-tools)
- [GeoPy](https://geopy.readthedocs.io/)

Data
- [Potsdam Open Data-Portal](https://opendata.potsdam.de)
- [OpenStreetMap](https://www.openstreetmap.org/)
- [GeoNames](https://www.geonames.org)
- [DataHub](https://datahub.io)
